# 5D Kerr-AdS spacetime with a Nambu-Goto string

## Generic case (a,b) in global AdS coordinates

This [SageMath](https://www.sagemath.org/) notebook is relative to the article *Heavy quarks in rotating plasma via holography* by Anastasia A. Golubtsova, Eric Gourgoulhon and Marina K. Usova, [arXiv:2107.11672](https://arxiv.org/abs/2107.11672).

The involved differential geometry computations are based on tools developed through the [SageManifolds](https://sagemanifolds.obspm.fr) project.

*NB:* a version of SageMath at least equal to 9.1 is required to run this notebook:

In [1]:
version()

'SageMath version 9.3, Release Date: 2021-05-09'

First we set up the notebook to display mathematical objects using LaTeX rendering:

In [2]:
%display latex

Since some computations are quite long, we ask for running them in parallel on 8 cores:

In [3]:
Parallelism().set(nproc=8)

## Spacetime manifold

We declare the Kerr-AdS spacetime as a 5-dimensional Lorentzian manifold:

In [4]:
M = Manifold(5, 'M', r'\mathcal{M}', structure='Lorentzian', metric_name='G')
print(M)

5-dimensional Lorentzian manifold M


Let us define **Boyer-Lindquist-type coordinates (rational polynomial version)** on $\mathcal{M}$, via the method `chart()`, the argument of which is a string expressing the coordinates names, their ranges (the default is $(-\infty,+\infty)$) and their LaTeX symbols:

In [5]:
BL.<t,r,mu,ph,ps> = M.chart(r't r:(0,+oo) mu:(0,1):\mu ph:(0,2*pi):\phi ps:(0,2*pi):\psi')
BL

Chart (M, (t, r, mu, ph, ps))

The coordinate $\mu$ is related to the standard Boyer-Lindquist coordinate $\theta$ by
$$ \mu = \cos\theta$$

The coordinate ranges are

In [6]:
BL.coord_range()

t: (-oo, +oo); r: (0, +oo); mu: (0, 1); ph: (0, 2*pi); ps: (0, 2*pi)

Note that contrary to the 4-dimensional case, the range of $\mu$ is $(0,1)$ only (cf. Sec. 1.2 of [R.C. Myers, arXiv:1111.1903](https://arxiv.org/abs/1111.1903) or Sec. 2 of [G.W. Gibbons, H. Lüb, Don N. Page, C.N. Pope, J. Geom. Phys. **53**, 49 (2005)](https://doi.org/10.1016/j.geomphys.2004.05.001)). In other words, the range of $\theta$ is $\left(0, \frac{\pi}{2}\right)$ only. 

## Metric tensor

The 4 parameters $m$, $a$, $b$ and $\ell$ of the Kerr-AdS spacetime are declared as symbolic variables, $a$ and $b$ being the two angular momentum parameters and $\ell$ being related to the cosmological constant by $\Lambda = - 6 \ell^2$:

In [7]:
var('m a b', domain='real')

(m, a, b)

In this notebook, we set
$$ \ell = 1$$

In [8]:
l = 1

In [9]:
assume(a >= 0, a < 1)
assume(b >= 0, b < 1)

Possible particular cases:

In [10]:
#b = a
#a = 0
#b = 0

Some auxiliary functions:

In [11]:
keep_Delta = False  # change to False to provide explicit expression for Delta_r, Xi_a, etc...

In [12]:
sig = (1 + r^2*l^2)/r^2
costh2 = mu^2
sinth2 = 1 - mu^2
rho2 = r^2 + a^2*mu^2 + b^2*sinth2
if keep_Delta:
    Delta_r = var('Delta_r', latex_name=r'\Delta_r', domain='real')
    Delta_th = var('Delta_th', latex_name=r'\Delta_\theta', domain='real')
    if a == b:
        Xi_a = var('Xi', latex_name=r'\Xi', domain='real')
        Xi_b = Xi_a
    else:
        Xi_a = var('Xi_a', latex_name=r'\Xi_a', domain='real')
        Xi_b = var('Xi_b', latex_name=r'\Xi_b', domain='real')
    #Delta_th = 1 - a^2*l^2*mu^2 - b^2*l^2*sinth2
    Xi_a = 1 - a^2*l^2
    Xi_b = 1 - b^2*l^2
else:
    Delta_r = (r^2+a^2)*(r^2+b^2)*sig - 2*m
    Delta_th = 1 - a^2*l^2*mu^2 - b^2*l^2*sinth2
    Xi_a = 1 - a^2*l^2
    Xi_b = 1 - b^2*l^2

The metric is set by its components in the coordinate frame associated with the Boyer-Lindquist-type coordinates, which is the current manifold's default frame. These components can be deduced from
Eq. (5.22) of the article [S.W. Hawking, C.J. Hunter & M.M. Taylor-Robinson, Phys. Rev. D **59**, 064005 (1999)](https://doi.org/10.1103/PhysRevD.59.064005) (the check of agreement with this equation is performed below):

In [13]:
G = M.metric()
tmp = 1/rho2*( -Delta_r + Delta_th*(a^2*sinth2 + b^2*mu^2) + a^2*b^2*sig )
G[0,0] = tmp.simplify_full()
tmp = a*sinth2/(rho2*Xi_a)*( Delta_r - (r^2+a^2)*(Delta_th + b^2*sig) )
G[0,3] = tmp.simplify_full()
tmp = b*mu^2/(rho2*Xi_b)*( Delta_r - (r^2+b^2)*(Delta_th + a^2*sig) )
G[0,4] = tmp.simplify_full()
G[1,1] = (rho2/Delta_r).simplify_full()
G[2,2] = (rho2/Delta_th/(1-mu^2)).simplify_full()
tmp = sinth2/(rho2*Xi_a^2)*( - Delta_r*a^2*sinth2 + (r^2+a^2)^2*(Delta_th + sig*b^2*sinth2) ) 
G[3,3] = tmp.simplify_full()
tmp = a*b*sinth2*mu^2/(rho2*Xi_a*Xi_b)*( - Delta_r + sig*(r^2+a^2)*(r^2+b^2) )
G[3,4] = tmp.simplify_full()
tmp = mu^2/(rho2*Xi_b^2)*( - Delta_r*b^2*mu^2 + (r^2+b^2)^2*(Delta_th + sig*a^2*mu^2) )
G[4,4] = tmp.simplify_full()

In [14]:
G.display_comp(only_nonredundant=True)

G_t,t = ((a^4 - 2*a^2*b^2 + b^4)*mu^4 - r^4 - (a^2 + 1)*b^2 - (a^4 + b^4 - (2*a^2 + 1)*b^2 + a^2)*mu^2 - (a^2 + b^2 + 1)*r^2 + 2*m)/((a^2 - b^2)*mu^2 + b^2 + r^2) 
G_t,ph = -(a^3*b^2 - (a^5 - a^3*b^2)*mu^4 - (a*mu^2 - a)*r^4 + (a^5 - 2*a^3*b^2 + 2*a*m)*mu^2 - (2*a*b^2*mu^2 + (a^3 - a*b^2)*mu^4 - a^3 - a*b^2)*r^2 - 2*a*m)/((a^2 - 1)*b^2 + (a^4 - (a^2 - 1)*b^2 - a^2)*mu^2 + (a^2 - 1)*r^2) 
G_t,ps = -(b*mu^2*r^4 + (a^2*b^3 - b^5)*mu^4 + (b^5 - 2*b*m)*mu^2 + (2*b^3*mu^2 + (a^2*b - b^3)*mu^4)*r^2)/(b^4 - (b^4 - (a^2 + 1)*b^2 + a^2)*mu^2 + (b^2 - 1)*r^2 - b^2) 
G_r,r = (r^4 + ((a^2 - b^2)*mu^2 + b^2)*r^2)/(r^6 + (a^2 + b^2 + 1)*r^4 + a^2*b^2 + ((a^2 + 1)*b^2 + a^2 - 2*m)*r^2) 
G_mu,mu = ((a^2 - b^2)*mu^2 + b^2 + r^2)/((a^2 - b^2)*mu^4 - (a^2 - 2*b^2 + 1)*mu^2 - b^2 + 1) 
G_ph,ph = ((a^6 - a^4 - (a^4 - a^2)*b^2 + 2*a^2*m)*mu^4 + ((a^2 - 1)*mu^2 - a^2 + 1)*r^4 - (a^4 - a^2)*b^2 + 2*a^2*m - (a^6 - a^4 - 2*(a^4 - a^2)*b^2 + 4*a^2*m)*mu^2 + (2*(a^2 - 1)*b^2*mu^2 + (a^4 - (a^2 - 1)*b^2 - a^2)*mu^4 - a^4 - (a^2 - 1)*b^2 + a^2)*r^2)/((a^4 - 2*a^2 + 1)*b^2 + (a^6 - 2*a^4 - (a^4 - 2*a^2 + 1)*b^2 + a^2)*mu^2 + (a^4 - 2*a^2 + 1)*r^2) 
G_ph,ps = -2*(a*b*m*mu^4 - a*b*m*mu^2)/((a^2 - 1)*b^4 - (a^2 - 1)*b^2 - ((a^2 - 1)*b^4 + a^4 - (a^4 - 1)*b^2 - a^2)*mu^2 + ((a^2 - 1)*b^2 - a^2 + 1)*r^2) 
G_ps,ps = -((b^2 - 1)*mu^2*r^4 - (b^6 - (a^2 + 1)*b^4 + a^2*b^2 + 2*b^2*m)*mu^4 + (b^6 - b^4)*mu^2 - ((b^4 - (a^2 + 1)*b^2 + a^2)*mu^4 - 2*(b^4 - b^2)*mu^2)*r^2)/(b^6 - 2*b^4 - (b^6 - (a^2 + 2)*b^4 + (2*a^2 + 1)*b^2 - a^2)*mu^2 + (b^4 - 2*b^2 + 1)*r^2 + b^2)

### Check of Eq. (2.9)

We need the 1-forms $\mathrm{d}t$, $\mathrm{d}r$, $\mathrm{d}\mu$, $\mathrm{d}\phi$ and $\mathrm{d}\psi$:

In [15]:
dt, dr, dmu, dph, dps = (BL.coframe()[i] for i in M.irange())
dt, dr, dmu, dph, dps

(1-form dt on the 5-dimensional Lorentzian manifold M,
 1-form dr on the 5-dimensional Lorentzian manifold M,
 1-form dmu on the 5-dimensional Lorentzian manifold M,
 1-form dph on the 5-dimensional Lorentzian manifold M,
 1-form dps on the 5-dimensional Lorentzian manifold M)

In [16]:
print(dt)

1-form dt on the 5-dimensional Lorentzian manifold M


In agreement with $\mu = \cos\theta$, we introduce the 1-form
$$\mathrm{d}\theta = - \mathrm{d}\mu /\sin\theta ,$$
with
$\sin\theta = \sqrt{1-\mu^2}$ since $\theta\in\left(0, \frac{\pi}{2}\right)$ :

In [17]:
dth = - 1/sqrt(1 - mu^2)*dmu

In [18]:
s1 = dt - a*sinth2/Xi_a*dph - b*costh2/Xi_b*dps
s1.display()

dt - (a*mu^2 - a)/(a^2 - 1) dph + b*mu^2/(b^2 - 1) dps

In [19]:
s2 = a*dt - (r^2 + a^2)/Xi_a*dph
s2.display()

a dt + (a^2 + r^2)/(a^2 - 1) dph

In [20]:
s3 = b*dt - (r^2 + b^2)/Xi_b*dps
s3.display()

b dt + (b^2 + r^2)/(b^2 - 1) dps

In [21]:
s4 = a*b*dt - b*(r^2 + a^2)*sinth2/Xi_a * dph - a*(r^2 + b^2)*costh2/Xi_b * dps
s4.display()

a*b dt - (a^2*b*mu^2 - a^2*b + (b*mu^2 - b)*r^2)/(a^2 - 1) dph + (a*b^2*mu^2 + a*mu^2*r^2)/(b^2 - 1) dps

In [22]:
G0 = - Delta_r/rho2 * s1*s1 + Delta_th*sinth2/rho2 * s2*s2 \
     + Delta_th*costh2/rho2 * s3*s3 + rho2/Delta_r * dr*dr \
     + rho2/Delta_th * dth*dth + sig/rho2 * s4*s4

Check of Eq. (2.9):

In [23]:
G0 == G

True

## Einstein equation

The Ricci tensor of $g$ is

In [24]:
if not keep_Delta:
    # Ric = G.ricci()
    # print(Ric)
    pass

In [25]:
if not keep_Delta:
    # show(Ric.display_comp(only_nonredundant=True))
    pass

Let us check that $g$ is a solution of the vacuum Einstein equation with the cosmological constant $\Lambda = - 6 \ell^2$:

In [26]:
Lambda = -6*l^2
if not keep_Delta:
    # print(Ric == 2/3*Lambda*G)
    pass

### Conformal metric at the boundary $r\to +\infty$ (check of Eq. (2.11))

The conformal metric:

In [27]:
H = G / (1 + r^2)
H.set_name('H')

In [28]:
H[1,1]

(r^4 + ((a^2 - b^2)*mu^2 + b^2)*r^2)/((r^6 + (a^2 + b^2 + 1)*r^4 + a^2*b^2 + ((a^2 + 1)*b^2 + a^2 - 2*m)*r^2)*(r^2 + 1))

Let us introduce a function to perform asymptotic expansions up to a given order:

In [29]:
u = var('u')
def asympt(xx, rr, order):
    r"""
    Expansion in terms of 1/rr

    INPUT:

    - ``xx`` -- symbolic expression to expand
    - ``rr`` -- symbolic variable, the inverse of which is the expansion small parameter
    - ``order`` -- order of the expansion

    OUTPUT:

    - symbolic expression representing ``xx`` truncated at degree ``order`` in terms
      of ``1/rr``

    """
    xx = xx.subs({rr: 1/u}).simplify_full()
    xx = xx.series(u, order+1).truncate().simplify_full()
    xx = xx.subs({u: 1/rr}).simplify_full()
    return xx    

Expansion to order $1/r^0$ provides the conformal metric on the boundary $r\to +\infty$:

In [30]:
H0 = M.sym_bilin_form_field(name='H_0')
for i in M.irange():
    for j in M.irange(i):
        H0[i, j] = asympt(H[i,j].expr(), r, 0)
H0.display()

H_0 = -dt*dt + (a*mu^2 - a)/(a^2 - 1) dt*dph - b*mu^2/(b^2 - 1) dt*dps + 1/((a^2 - b^2)*mu^4 - (a^2 - 2*b^2 + 1)*mu^2 - b^2 + 1) dmu*dmu + (a*mu^2 - a)/(a^2 - 1) dph*dt + (mu^2 - 1)/(a^2 - 1) dph*dph - b*mu^2/(b^2 - 1) dps*dt - mu^2/(b^2 - 1) dps*dps

This agrees with Eq. (2.11); in particular, we have

In [31]:
H0[2,2].factor()

1/((a^2*mu^2 - b^2*mu^2 + b^2 - 1)*(mu + 1)*(mu - 1))

## Global  AdS coordinates

In [32]:
ADS.<T,y,ch,Ph,Ps> = M.chart(r'T y:(0,+oo) ch:(0,1):\chi Ph:(0,2*pi):\Phi Ps:(0,2*pi):\Psi')
ADS

Chart (M, (T, y, ch, Ph, Ps))

In [33]:
ADS.coord_range()

T: (-oo, +oo); y: (0, +oo); ch: (0, 1); Ph: (0, 2*pi); Ps: (0, 2*pi)

The transition from the Boyer-Lindquist coordinates to the global AdS coordinates is derived from Eq. (5.24) of [S.W. Hawking, C.J. Hunter & M.M. Taylor-Robinson, Phys. Rev. D **59**, 064005 (1999)](https://doi.org/10.1103/PhysRevD.59.064005):

The following assumptions are required to perform simplifications:

In [34]:
if not (a == 0 or b == 0 or b == a):
    assume((a^2 - b^2)*mu^2 + b^2 + r^2 > 0)
    assume((a^2 - b^2)*ch^2 - a^2 + 1 > 0)

In [35]:
assumptions()

[t is real,
 r is real,
 r > 0,
 mu is real,
 mu > 0,
 mu < 1,
 ph is real,
 ph > 0,
 ph < 2*pi,
 ps is real,
 ps > 0,
 ps < 2*pi,
 m is real,
 a is real,
 b is real,
 a >= 0,
 a < 1,
 b >= 0,
 b < 1,
 T is real,
 y is real,
 y > 0,
 ch is real,
 ch > 0,
 ch < 1,
 Ph is real,
 Ph > 0,
 Ph < 2*pi,
 Ps is real,
 Ps > 0,
 Ps < 2*pi,
 (a^2 - b^2)*mu^2 + b^2 + r^2 > 0,
 (a^2 - b^2)*ch^2 - a^2 + 1 > 0]

We import the function `simplify_sqrt_real` to simplify some square roots, which would not be simplified with `simplify_full`:

In [36]:
from sage.manifolds.utilities import simplify_sqrt_real

In [37]:
ys = sqrt(Xi_b*(r^2 + a^2)*(1-mu^2) + Xi_a*(r^2 + b^2)*mu^2) \
     /(sqrt(Xi_a)*sqrt(Xi_b))
ys = simplify_sqrt_real(ys.simplify_full())

chs = sqrt(Xi_a)*sqrt(r^2 + b^2)*mu / sqrt(Xi_a*(r^2 + b^2)*mu^2 
                                           + Xi_b*(r^2 + a^2)*(1 - mu^2))
chs = simplify_sqrt_real(chs.simplify_full())

In [38]:
ys

sqrt(-a^2*b^2 - (a^2 - b^2)*mu^2 - ((a^2 - b^2)*mu^2 + b^2 - 1)*r^2 + a^2)/(sqrt(a + 1)*sqrt(-a + 1)*sqrt(b + 1)*sqrt(-b + 1))

In [39]:
chs

sqrt(b^2 + r^2)*sqrt(a + 1)*sqrt(-a + 1)*mu/sqrt(-a^2*b^2 - (a^2 - b^2)*mu^2 - ((a^2 - b^2)*mu^2 + b^2 - 1)*r^2 + a^2)

In [40]:
BL_to_ADS = BL.transition_map(ADS, [t, ys, chs, ph + a*t, ps + b*t])
BL_to_ADS.display()

T = t
y = sqrt(-a^2*b^2 - (a^2 - b^2)*mu^2 - ((a^2 - b^2)*mu^2 + b^2 - 1)*r^2 + a^2)/(sqrt(a + 1)*sqrt(-a + 1)*sqrt(b + 1)*sqrt(-b + 1))
ch = sqrt(b^2 + r^2)*sqrt(a + 1)*sqrt(-a + 1)*mu/sqrt(-a^2*b^2 - (a^2 - b^2)*mu^2 - ((a^2 - b^2)*mu^2 + b^2 - 1)*r^2 + a^2)
Ph = a*t + ph
Ps = b*t + ps

In [41]:
Discr = (a^2 + b^2 + y^2*((b^2 - a^2)*ch^2 + a^2 - 1))^2 - 4*a^2*b^2 \
        + 4*y^2*((a^2 - b^2)*ch^2 + b^2*(1 - a^2))
Discr = Discr.simplify_full()
Discr

((a^4 - 2*a^2*b^2 + b^4)*ch^4 + a^4 - 2*(a^4 - (a^2 - 1)*b^2 - a^2)*ch^2 - 2*a^2 + 1)*y^4 + a^4 - 2*a^2*b^2 + b^4 + 2*(a^4 - (a^2 - 1)*b^2 - (a^4 - b^4 - 2*a^2 + 2*b^2)*ch^2 - a^2)*y^2

In [42]:
sqrDiscr = simplify_sqrt_real(sqrt(Discr))

In [43]:
rs2 = 1/2*(y^2*((a^2 - b^2)*ch^2 + 1 - a^2) - a^2 - b^2 + sqrDiscr)
rs2 = rs2.simplify_full()
rs2

1/2*((a^2 - b^2)*ch^2 - a^2 + 1)*y^2 - 1/2*a^2 - 1/2*b^2 + 1/2*sqrt(((a^4 - 2*a^2*b^2 + b^4)*ch^4 + a^4 - 2*(a^4 - (a^2 - 1)*b^2 - a^2)*ch^2 - 2*a^2 + 1)*y^4 + a^4 - 2*a^2*b^2 + b^4 + 2*(a^4 - (a^2 - 1)*b^2 - (a^4 - b^4 - 2*a^2 + 2*b^2)*ch^2 - a^2)*y^2)

Check:

In [44]:
s = (rs2 + a^2)*(rs2 + b^2) - (rs2 + a^2)*(1 - b^2)*y^2*ch^2 \
    - (rs2 + b^2)*(1 - a^2)*y^2*(1 - ch^2) == 0
s.simplify_full()

0 == 0

In [45]:
rs =  simplify_sqrt_real(sqrt(rs2))

In [46]:
mus = sqrt(1 - b^2)/sqrt(rs2 + b^2)*y*ch
mus = simplify_sqrt_real(mus.simplify_full())
mus

sqrt(2)*sqrt(b + 1)*sqrt(-b + 1)*ch*y/sqrt(((a^2 - b^2)*ch^2 - a^2 + 1)*y^2 - a^2 + b^2 + sqrt(((a^4 - 2*a^2*b^2 + b^4)*ch^4 + a^4 - 2*(a^4 - (a^2 - 1)*b^2 - a^2)*ch^2 - 2*a^2 + 1)*y^4 + a^4 - 2*a^2*b^2 + b^4 + 2*(a^4 - (a^2 - 1)*b^2 - (a^4 - b^4 - 2*a^2 + 2*b^2)*ch^2 - a^2)*y^2))

In [47]:
BL_to_ADS.set_inverse(T, rs, mus, Ph - a*T, Ps - b*T, 
                      verbose=True)
BL_to_ADS.inverse().display()

Check of the inverse coordinate transformation:
  t == t  *passed*
  r == r  *passed*
  mu == mu  *passed*
  ph == ph  *passed*
  ps == ps  *passed*
  T == T  *passed*
  y == y  *passed*
  ch == ch  *passed*
  Ph == Ph  *passed*
  Ps == Ps  *passed*


t = T
r = 1/2*sqrt(2)*sqrt(((a^2 - b^2)*ch^2 - a^2 + 1)*y^2 - a^2 - b^2 + sqrt(((a^4 - 2*a^2*b^2 + b^4)*ch^4 + a^4 - 2*(a^4 - (a^2 - 1)*b^2 - a^2)*ch^2 - 2*a^2 + 1)*y^4 + a^4 - 2*a^2*b^2 + b^4 + 2*(a^4 - (a^2 - 1)*b^2 - (a^4 - b^4 - 2*a^2 + 2*b^2)*ch^2 - a^2)*y^2))
mu = sqrt(2)*sqrt(b + 1)*sqrt(-b + 1)*ch*y/sqrt(((a^2 - b^2)*ch^2 - a^2 + 1)*y^2 - a^2 + b^2 + sqrt(((a^4 - 2*a^2*b^2 + b^4)*ch^4 + a^4 - 2*(a^4 - (a^2 - 1)*b^2 - a^2)*ch^2 - 2*a^2 + 1)*y^4 + a^4 - 2*a^2*b^2 + b^4 + 2*(a^4 - (a^2 - 1)*b^2 - (a^4 - b^4 - 2*a^2 + 2*b^2)*ch^2 - a^2)*y^2))
ph = -T*a + Ph
ps = -T*b + Ps

In [48]:
BL_to_ADS.jacobian()

[                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                           1                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                            0                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                            0                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                            0                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                            0]
[                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                           0                                                                                                                                                                                                                                                                                                                                                               -((a^2 - b^2)*mu^2 + b^2 - 1)*r/(sqrt(-a^2*b^2 - (a^2 - b^2)*mu^2 - ((a^2 - b^2)*mu^2 + b^2 - 1)*r^2 + a^2)*sqrt(a + 1)*sqrt(-a + 1)*sqrt(b + 1)*sqrt(-b + 1))                                                                                                                                                                                                                                                                                                                                                        -((a^2 - b^2)*mu*r^2 + (a^2 - b^2)*mu)/(sqrt(-a^2*b^2 - (a^2 - b^2)*mu^2 - ((a^2 - b^2)*mu^

In [49]:
BL_to_ADS.inverse().jacobian()

[                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                      1                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                       0                                                                                                                                                                                                                                                                                                                                                                                                                                                

*Remark:* despite the rather complicated relation between $y$ and $(r,\mu)$, the ratio $(1 + r^2)/(1 + y^2)$ depends only on $\mu$ and takes a simple form:
$$
    \frac{1 + r^2}{1 + y^2} = \frac{(1 - a^2) (1 - b^2)}{1 - a^2\mu^2 - b^2 (1 - \mu^2)}
$$
Indeed:

In [50]:
((1 + r^2)/(1 + ys^2)).simplify_full().factor()

-(a + 1)*(a - 1)*(b + 1)*(b - 1)/(a^2*mu^2 - b^2*mu^2 + b^2 - 1)

### Metric components in global ADS coordinates

For generic values of $(a,b)$, Sage does not succeed in computing the components of the 
metric tensor $G$ in a reasonable time.
Only for $a=b$ or $b=0$ it manages to do so. For $b=0$, the expression is cumbersome, but
for $a=b$, one gets a rather simple expression:

In [51]:
if a == b:
    show(G.display_comp(chart=ADS, only_nonredundant=True))

## Asymptotic form of the metric in ADS coordinates (check of Eq. (2.17))

For $y\to +\infty$, the metric tensor $G$ can be approximated by $K$, the expression of the latter in ADS coordinates being given by Eq. (3.27) of [Gibbons, Perry & Pope, CQG **22**, 1503 (2005)](https://doi.org/10.1088/0264-9381/22/9/002) ([arXiv:hep-th/0408217](https://arxiv.org/abs/hep-th/0408217)) (our Eq. (2.17)):

In [52]:
M.set_default_frame(ADS.frame())
M.set_default_chart(ADS)

In [53]:
K = M.lorentzian_metric('K')
Delta = var('Delta', latex_name=r'\Delta', domain='real')
K[0, 0] = -1 - y^2 + 2*m/(Delta^3*y^2)
K[0, 3] = -2*m*a*(1 - ch^2)/(Delta^3*y^2)
K[0, 4] = -2*m*b*ch^2/(Delta^3*y^2)
K[1, 1] =  1/(1 + y^2 - 2*m/(Delta^3*y^2))
K[2, 2] = y^2/(1 - ch^2)
K[3, 3] = y^2*(1 - ch^2) + 2*m*a^2*(1 - ch^2)^2/(Delta^3*y^2)
K[3, 4] = 2*m*a*b*ch^2*(1 - ch^2)/(Delta^3*y^2)
K[4, 4] = y^2*ch^2 + 2*m*b^2*ch^4/(Delta^3*y^2)
K.display()

K = (-y^2 + 2*m/(Delta^3*y^2) - 1) dT*dT + 2*(ch^2 - 1)*a*m/(Delta^3*y^2) dT*dPh - 2*b*ch^2*m/(Delta^3*y^2) dT*dPs + 1/(y^2 - 2*m/(Delta^3*y^2) + 1) dy*dy - y^2/(ch^2 - 1) dch*dch + 2*(ch^2 - 1)*a*m/(Delta^3*y^2) dPh*dT + (-(ch^2 - 1)*y^2 + 2*(ch^2 - 1)^2*a^2*m/(Delta^3*y^2)) dPh*dPh - 2*(ch^2 - 1)*a*b*ch^2*m/(Delta^3*y^2) dPh*dPs - 2*b*ch^2*m/(Delta^3*y^2) dPs*dT - 2*(ch^2 - 1)*a*b*ch^2*m/(Delta^3*y^2) dPs*dPh + (ch^2*y^2 + 2*b^2*ch^4*m/(Delta^3*y^2)) dPs*dPs

In the above expression, we do not have specified $\Delta$. Its explicit expression in terms of $a$, $b$ and $\chi$ is

In [54]:
Delta_abc = (1 - a^2*(1 - ch^2) - b^2*ch^2).simplify_full()
Delta_abc

(a^2 - b^2)*ch^2 - a^2 + 1

### Check of Eq. (2.17) for $a=b$:

For $a=b$, $G$ and $K$ differ only by a term proportional to $\mathrm{d}y\otimes\mathrm{d}y$:

In [55]:
if a == b:
    K0 = K.copy(name='K')
    K0.apply_map(lambda x: x.subs({Delta: Delta_abc}))
    GmK = G - K0
    show(GmK.display())

This difference is only of order $O(1/y^6)$:

In [56]:
if a == b:
    es = sum(asympt(GmK[1,1].expr(), y, k) for k in range(9))
    show(es)

### Setting the metric to its asymptotic form:

In [57]:
G.set(K)
G.display()

G = (-y^2 + 2*m/(Delta^3*y^2) - 1) dT*dT + 2*(ch^2 - 1)*a*m/(Delta^3*y^2) dT*dPh - 2*b*ch^2*m/(Delta^3*y^2) dT*dPs + 1/(y^2 - 2*m/(Delta^3*y^2) + 1) dy*dy - y^2/(ch^2 - 1) dch*dch + 2*(ch^2 - 1)*a*m/(Delta^3*y^2) dPh*dT + (-(ch^2 - 1)*y^2 + 2*(ch^2 - 1)^2*a^2*m/(Delta^3*y^2)) dPh*dPh - 2*(ch^2 - 1)*a*b*ch^2*m/(Delta^3*y^2) dPh*dPs - 2*b*ch^2*m/(Delta^3*y^2) dPs*dT - 2*(ch^2 - 1)*a*b*ch^2*m/(Delta^3*y^2) dPs*dPh + (ch^2*y^2 + 2*b^2*ch^4*m/(Delta^3*y^2)) dPs*dPs

In [58]:
G.display_comp()

G_T,T = -y^2 + 2*m/(Delta^3*y^2) - 1 
G_T,Ph = 2*(ch^2 - 1)*a*m/(Delta^3*y^2) 
G_T,Ps = -2*b*ch^2*m/(Delta^3*y^2) 
G_y,y = 1/(y^2 - 2*m/(Delta^3*y^2) + 1) 
G_ch,ch = -y^2/(ch^2 - 1) 
G_Ph,T = 2*(ch^2 - 1)*a*m/(Delta^3*y^2) 
G_Ph,Ph = -(ch^2 - 1)*y^2 + 2*(ch^2 - 1)^2*a^2*m/(Delta^3*y^2) 
G_Ph,Ps = -2*(ch^2 - 1)*a*b*ch^2*m/(Delta^3*y^2) 
G_Ps,T = -2*b*ch^2*m/(Delta^3*y^2) 
G_Ps,Ph = -2*(ch^2 - 1)*a*b*ch^2*m/(Delta^3*y^2) 
G_Ps,Ps = ch^2*y^2 + 2*b^2*ch^4*m/(Delta^3*y^2)

## String worldsheet

The string worldsheet as a 2-dimensional Lorentzian submanifold of $\mathcal{M}$:

In [59]:
W = Manifold(2, 'W', ambient=M, structure='Lorentzian')
print(W)

2-dimensional Lorentzian submanifold W immersed in the 5-dimensional Lorentzian manifold M


Let us assume that the string worldsheet is parametrized by $(T,y)$:

In [60]:
XW.<T,y> = W.chart(r'T y:(0,+oo)')
XW

Chart (W, (T, y))

The string embedding in Kerr-AdS spacetime, as an expansion about a 
straight string solution in AdS (Eq. (4.27) of the paper):

In [61]:
ch0 = var('ch0', latex_name=r'\chi_0', domain='real')
Phi0 = var('Phi0', latex_name=r'\Phi_0', domain='real')
Psi0 = var('Psi0', latex_name=r'\Psi_0', domain='real')

cosTh0 = ch0
sinTh0 = sqrt(1 - ch0^2)

ch_s = ch0 + (a+b)^2*function('chi_1')(y)
Ph_s = Phi0 + a*T + a*function('Phi_1')(y)
Ps_s = Psi0 + b*T + b*function('Psi_1')(y)

F = W.diff_map(M, {(XW, ADS): [T, y, ch_s, Ph_s, Ps_s]}, name='F') 

W.set_embedding(F)

F.display(XW, ADS)

F: W --> M
   (T, y) |--> (T, y, ch, Ph, Ps) = (T, y, (a + b)^2*chi_1(y) + ch0, T*a + a*Phi_1(y) + Phi0, T*b + b*Psi_1(y) + Psi0)

In [62]:
F.jacobian_matrix()

[                                    1                                     0]
[                                    0                                     1]
[                                    0 (a^2 + 2*a*b + b^2)*diff(chi_1(y), y)]
[                                    a                   a*diff(Phi_1(y), y)]
[                                    b                   b*diff(Psi_1(y), y)]

### Induced metric on the string worldsheet

The string worldsheet metric is the metric $g$ induced by the spacetime metric $G$, i.e. the pullback of $G$ by the embedding $F$:

Because of the bug [#27492](https://trac.sagemath.org/ticket/27492), which impedes parallel computations involving symbolic functions, such as $\chi_1$, we set back to serial computations:

In [63]:
Parallelism().set(nproc=1)  

In [64]:
g = W.induced_metric()

In [65]:
g[0,0]

(8*(a^10 + 6*a^9*b + 13*a^8*b^2 + 8*a^7*b^3 - 14*a^6*b^4 - 28*a^5*b^5 - 14*a^4*b^6 + 8*a^3*b^7 + 13*a^2*b^8 + 6*a*b^9 + b^10)*ch0*m*chi_1(y)^3 + 2*(a^12 + 8*a^11*b + 26*a^10*b^2 + 40*a^9*b^3 + 15*a^8*b^4 - 48*a^7*b^5 - 84*a^6*b^6 - 48*a^5*b^7 + 15*a^4*b^8 + 40*a^3*b^9 + 26*a^2*b^10 + 8*a*b^11 + b^12)*m*chi_1(y)^4 - Delta^3*y^2 + (Delta^3*a^2 - Delta^3 - (Delta^3*a^2 - Delta^3*b^2)*ch0^2)*y^4 - ((Delta^3*a^6 + 4*Delta^3*a^5*b + 5*Delta^3*a^4*b^2 - 5*Delta^3*a^2*b^4 - 4*Delta^3*a*b^5 - Delta^3*b^6)*y^4 + 4*(a^8 - (a^2 - 1)*b^6 - a^6 - 4*(a^3 - a)*b^5 - 5*(a^4 - a^2)*b^4 + 5*(a^6 - a^4)*b^2 - 3*(a^8 + 4*a^7*b + 4*a^6*b^2 - 4*a^5*b^3 - 10*a^4*b^4 - 4*a^3*b^5 + 4*a^2*b^6 + 4*a*b^7 + b^8)*ch0^2 + 4*(a^7 - a^5)*b)*m)*chi_1(y)^2 + 2*((a^4 - 2*a^2*b^2 + b^4)*ch0^4 + a^4 - 2*(a^4 - (a^2 - 1)*b^2 - a^2)*ch0^2 - 2*a^2 + 1)*m - 2*((Delta^3*a^4 + 2*Delta^3*a^3*b - 2*Delta^3*a*b^3 - Delta^3*b^4)*ch0*y^4 - 4*((a^6 + 2*a^5*b - a^4*b^2 - 4*a^3*b^3 - a^2*b^4 + 2*a*b^5 + b^6)*ch0^3 - (a^6 - (a^2 - 1)*b^4 - a^4 - 2*(a^3 - a)*b^3 + 2*(a^5 - a^3)*b)*ch0)*m)*chi_1(y))/(Delta^3*y^2)

## Nambu-Goto action

The determinant of $g$ is

In [66]:
detg = g.determinant().expr()

Let us define a function for expansions in $a$ and $b$ up to a given order:

In [67]:
eps = var('eps', latex_name=r'\epsilon', domain='real')
def expand_ab(expr, order):
    res = expr.subs({a: eps*a, b: eps*b})
    res = res.series(eps, order+1).truncate()
    res = res.subs({eps: 1}).simplify_full()
    return res

In [68]:
Delta3_4 = expand_ab((Delta_abc)^3, 4)
Delta3_4

3*(a^4 - 2*a^2*b^2 + b^4)*ch^4 + 3*a^4 - 3*(2*a^4 - (2*a^2 - 1)*b^2 - a^2)*ch^2 - 3*a^2 + 1

In [69]:
Delta6_4 = expand_ab((Delta_abc)^6, 4)
Delta6_4

15*(a^4 - 2*a^2*b^2 + b^4)*ch^4 + 15*a^4 - 6*(5*a^4 - (5*a^2 - 1)*b^2 - a^2)*ch^2 - 6*a^2 + 1

Expanding at fourth order in $a$ and $b$ (will be required latter):

In [70]:
detg_4 = expand_ab(detg, 4)
detg_4 = detg_4.subs({Delta^3: Delta3_4, Delta^6: Delta6_4})
detg_4 = detg_4.simplify_full()
detg_4 = expand_ab(detg_4, 4)

For the time being, only the expansion at second order in $a$ is required:

In [71]:
detg_2 = expand_ab(detg_4, 2)
detg_2 

-(((a^2 - b^2)*ch0^2 - a^2 + 1)*y^4 - ((a^2*ch0^2 - a^2)*y^8 + 2*(a^2*ch0^2 - a^2)*y^6 + (a^2*ch0^2 - a^2 - 4*(a^2*ch0^2 - a^2)*m)*y^4 - 4*(a^2*ch0^2 - a^2)*m*y^2 + 4*(a^2*ch0^2 - a^2)*m^2)*diff(Phi_1(y), y)^2 + (b^2*ch0^2*y^8 + 2*b^2*ch0^2*y^6 - 4*b^2*ch0^2*m*y^2 + 4*b^2*ch0^2*m^2 - (4*b^2*ch0^2*m - b^2*ch0^2)*y^4)*diff(Psi_1(y), y)^2 - 2*(2*(a^2 - b^2)*ch0^2 - 2*a^2 + 1)*m + y^2)/(y^4 + y^2 - 2*m)

The Nambu-Goto Lagrangian at second order in $a$ and $b$:

In [72]:
L_2 = expand_ab(sqrt(-detg_2), 2)
L_2

1/2*(((a^2 - b^2)*ch0^2 - a^2 + 2)*y^4 - ((a^2*ch0^2 - a^2)*y^8 + 2*(a^2*ch0^2 - a^2)*y^6 + (a^2*ch0^2 - a^2 - 4*(a^2*ch0^2 - a^2)*m)*y^4 - 4*(a^2*ch0^2 - a^2)*m*y^2 + 4*(a^2*ch0^2 - a^2)*m^2)*diff(Phi_1(y), y)^2 + (b^2*ch0^2*y^8 + 2*b^2*ch0^2*y^6 - 4*b^2*ch0^2*m*y^2 + 4*b^2*ch0^2*m^2 - (4*b^2*ch0^2*m - b^2*ch0^2)*y^4)*diff(Psi_1(y), y)^2 - 4*((a^2 - b^2)*ch0^2 - a^2 + 1)*m + 2*y^2)/(y^4 + y^2 - 2*m)

In [73]:
L_2.numerator()

-a^2*ch0^2*y^8*diff(Phi_1(y), y)^2 + b^2*ch0^2*y^8*diff(Psi_1(y), y)^2 - 2*a^2*ch0^2*y^6*diff(Phi_1(y), y)^2 + a^2*y^8*diff(Phi_1(y), y)^2 + 2*b^2*ch0^2*y^6*diff(Psi_1(y), y)^2 + 4*a^2*ch0^2*m*y^4*diff(Phi_1(y), y)^2 - 4*b^2*ch0^2*m*y^4*diff(Psi_1(y), y)^2 - a^2*ch0^2*y^4*diff(Phi_1(y), y)^2 + 2*a^2*y^6*diff(Phi_1(y), y)^2 + b^2*ch0^2*y^4*diff(Psi_1(y), y)^2 + 4*a^2*ch0^2*m*y^2*diff(Phi_1(y), y)^2 - 4*a^2*m*y^4*diff(Phi_1(y), y)^2 - 4*b^2*ch0^2*m*y^2*diff(Psi_1(y), y)^2 + a^2*ch0^2*y^4 - b^2*ch0^2*y^4 - 4*a^2*ch0^2*m^2*diff(Phi_1(y), y)^2 + a^2*y^4*diff(Phi_1(y), y)^2 + 4*b^2*ch0^2*m^2*diff(Psi_1(y), y)^2 - 4*a^2*m*y^2*diff(Phi_1(y), y)^2 - a^2*y^4 + 4*a^2*m^2*diff(Phi_1(y), y)^2 - 4*a^2*ch0^2*m + 4*b^2*ch0^2*m + 2*y^4 + 4*a^2*m + 2*y^2 - 4*m

In [74]:
L_2.denominator()

2*y^4 + 2*y^2 - 4*m

###  Euler-Lagrange equations

In [75]:
def euler_lagrange(lagr, qs, var):
    r"""
    Derive the Euler-Lagrange equations from a given Lagrangian.

    INPUT:

    - ``lagr`` -- symbolic expression representing the Lagrangian density
    - ``qs`` -- either a single symbolic function or a list/tuple of
      symbolic functions, representing the `q`'s; these functions must
      appear in ``lagr`` up to at most their first derivatives
    - ``var`` -- either a single variable, typically `t` (1-dimensional
      problem) or a list/tuple of symbolic variables

    OUTPUT:

    - list of Euler-Lagrange equations; if only one function is involved, the
      single Euler-Lagrannge equation is returned instead.

    """
    if not isinstance(qs, (list, tuple)):
        qs = [qs]
    if not isinstance(var, (list, tuple)):
        var = [var]
    n = len(qs)
    d = len(var)
    qv = [SR.var('qxxxx{}'.format(q)) for q in qs]
    dqv = [[SR.var('qxxxx{}_{}'.format(q, v)) for v in var] for q in qs]
    subs = {qs[i](*var): qv[i] for i in range(n)}
    subs_inv = {qv[i]: qs[i](*var) for i in range(n)}
    for i in range(n):
        subs.update({diff(qs[i](*var), var[j]): dqv[i][j]
                     for j in range(d)})
        subs_inv.update({dqv[i][j]: diff(qs[i](*var), var[j])
                         for j in range(d)})
    lg = lagr.substitute(subs)
    eqs = []
    for i in range(n):
        dLdq = diff(lg, qv[i]).simplify_full()
        dLdq = dLdq.substitute(subs_inv)
        ddL = 0
        for j in range(d):
            h =  diff(lg, dqv[i][j]).simplify_full()
            h = h.substitute(subs_inv)
            ddL += diff(h, var[j])
        eqs.append((dLdq - ddL).simplify_full() == 0)
    if n == 1:
        return eqs[0]
    return eqs

We compute the Euler-Lagrange equations from $L_2$ for $\Phi_1$ and $\Psi_1$:

In [76]:
eqs = euler_lagrange(L_2, [Phi_1, Psi_1], y)
eqs

[2*(2*(a^2*ch0^2 - a^2)*y^3 + (a^2*ch0^2 - a^2)*y)*diff(Phi_1(y), y) + ((a^2*ch0^2 - a^2)*y^4 + (a^2*ch0^2 - a^2)*y^2 - 2*(a^2*ch0^2 - a^2)*m)*diff(Phi_1(y), y, y) == 0,
 -2*(2*b^2*ch0^2*y^3 + b^2*ch0^2*y)*diff(Psi_1(y), y) - (b^2*ch0^2*y^4 + b^2*ch0^2*y^2 - 2*b^2*ch0^2*m)*diff(Psi_1(y), y, y) == 0]

#### Solving the equation for $\Phi_1$ (Eq. (4.29))

In [77]:
eq_Phi1 = eqs[0]
eq_Phi1

2*(2*(a^2*ch0^2 - a^2)*y^3 + (a^2*ch0^2 - a^2)*y)*diff(Phi_1(y), y) + ((a^2*ch0^2 - a^2)*y^4 + (a^2*ch0^2 - a^2)*y^2 - 2*(a^2*ch0^2 - a^2)*m)*diff(Phi_1(y), y, y) == 0

In [78]:
eq_Phi1 = (eq_Phi1/(a^2*(ch0^2-1))).simplify_full()
eq_Phi1

2*(2*y^3 + y)*diff(Phi_1(y), y) + (y^4 + y^2 - 2*m)*diff(Phi_1(y), y, y) == 0

In [79]:
Phi1_sol(y) = desolve(eq_Phi1, Phi_1(y), ivar=y)
Phi1_sol(y)

_K1*integrate(1/(y^4 + y^2 - 2*m), y) + _K2

We recover Eqs. (4.29) with $K_1 = \mathfrak{p}$ and $K_2=0$.

The symbolic constants $K_1$ and $K_2$ are actually denoted `_K1` and `_K2` by SageMath, as `print` reveals:

In [80]:
print(Phi1_sol(y))

_K1*integrate(1/(y^4 + y^2 - 2*m), y) + _K2


Hence we perform the substitutions with `SR.var('_K1')` and `SR.var('_K2')`:

In [81]:
pf = var("pf", latex_name=r"\mathfrak{p}", domain='real')
Phi1_sol(y) = Phi1_sol(y).subs({SR.var('_K1'): pf, SR.var('_K2'): 0})
Phi1_sol(y)

pf*integrate(1/(y^4 + y^2 - 2*m), y)

#### Solving the equation for $\Psi_1$  (Eq. (4.29))

In [82]:
eq_Psi1 = eqs[1]
eq_Psi1

-2*(2*b^2*ch0^2*y^3 + b^2*ch0^2*y)*diff(Psi_1(y), y) - (b^2*ch0^2*y^4 + b^2*ch0^2*y^2 - 2*b^2*ch0^2*m)*diff(Psi_1(y), y, y) == 0

In [83]:
eq_Phi1 = (eq_Psi1/(b^2*ch0^2)).simplify_full()
eq_Phi1

-2*(2*y^3 + y)*diff(Psi_1(y), y) - (y^4 + y^2 - 2*m)*diff(Psi_1(y), y, y) == 0

In [84]:
Psi1_sol(y) = desolve(eq_Psi1, Psi_1(y), ivar=y)
Psi1_sol(y)

_K1*integrate(1/(y^4 + y^2 - 2*m), y) + _K2

We recover Eq. (4.29) with $K_1 = \mathfrak{q}$ and $K_2=0$.

In [85]:
qf = var('qf', latex_name=r"\mathfrak{q}", domain='real')
Psi1_sol(y) = Psi1_sol(y).subs({SR.var('_K1'): qf, SR.var('_K2'): 0})
Psi1_sol(y)

qf*integrate(1/(y^4 + y^2 - 2*m), y)

### Nambu-Goto Lagrangian at fourth order in $a$ and $b$

In [86]:
L_4 = expand_ab(sqrt(-detg_4), 4)

In [87]:
eqs = euler_lagrange(L_4, [Phi_1, Psi_1, chi_1], y)

### The equation for $\chi_1$

In [88]:
eq_chi1 = eqs[2]
eq_chi1

(((a^4 + 2*a^3*b - 2*a*b^3 - b^4)*ch0^3 - (a^4 + 2*a^3*b - 2*a*b^3 - b^4)*ch0)*y^4 - (((a^4 + 2*a^3*b + a^2*b^2)*ch0^3 - (a^4 + 2*a^3*b + a^2*b^2)*ch0)*y^8 + 2*((a^4 + 2*a^3*b + a^2*b^2)*ch0^3 - (a^4 + 2*a^3*b + a^2*b^2)*ch0)*y^6 + ((a^4 + 2*a^3*b + a^2*b^2)*ch0^3 - (a^4 + 2*a^3*b + a^2*b^2)*ch0 - 4*((a^4 + 2*a^3*b + a^2*b^2)*ch0^3 - (a^4 + 2*a^3*b + a^2*b^2)*ch0)*m)*y^4 - 4*((a^4 + 2*a^3*b + a^2*b^2)*ch0^3 - (a^4 + 2*a^3*b + a^2*b^2)*ch0)*m*y^2 + 4*((a^4 + 2*a^3*b + a^2*b^2)*ch0^3 - (a^4 + 2*a^3*b + a^2*b^2)*ch0)*m^2)*diff(Phi_1(y), y)^2 + (((a^2*b^2 + 2*a*b^3 + b^4)*ch0^3 - (a^2*b^2 + 2*a*b^3 + b^4)*ch0)*y^8 + 2*((a^2*b^2 + 2*a*b^3 + b^4)*ch0^3 - (a^2*b^2 + 2*a*b^3 + b^4)*ch0)*y^6 + ((a^2*b^2 + 2*a*b^3 + b^4)*ch0^3 - (a^2*b^2 + 2*a*b^3 + b^4)*ch0 - 4*((a^2*b^2 + 2*a*b^3 + b^4)*ch0^3 - (a^2*b^2 + 2*a*b^3 + b^4)*ch0)*m)*y^4 - 4*((a^2*b^2 + 2*a*b^3 + b^4)*ch0^3 - (a^2*b^2 + 2*a*b^3 + b^4)*ch0)*m*y^2 + 4*((a^2*b^2 + 2*a*b^3 + b^4)*ch0^3 - (a^2*b^2 + 2*a*b^3 + b^4)*ch0)*m^2)*diff(Psi_1(y), y)^2 - 4*((a^4 + 2*a^3*b - 2*a*b^3 - b^4)*ch0^3 - (a^4 + 2*a^3*b - 2*a*b^3 - b^4)*ch0)*m + 2*(2*(a^4 + 4*a^3*b + 6*a^2*b^2 + 4*a*b^3 + b^4)*y^7 + 3*(a^4 + 4*a^3*b + 6*a^2*b^2 + 4*a*b^3 + b^4)*y^5 + (a^4 + 4*a^3*b + 6*a^2*b^2 + 4*a*b^3 + b^4 - 4*(a^4 + 4*a^3*b + 6*a^2*b^2 + 4*a*b^3 + b^4)*m)*y^3 - 2*(a^4 + 4*a^3*b + 6*a^2*b^2 + 4*a*b^3 + b^4)*m*y)*diff(chi_1(y), y) + ((a^4 + 4*a^3*b + 6*a^2*b^2 + 4*a*b^3 + b^4)*y^8 + 2*(a^4 + 4*a^3*b + 6*a^2*b^2 + 4*a*b^3 + b^4)*y^6 + (a^4 + 4*a^3*b + 6*a^2*b^2 + 4*a*b^3 + b^4 - 4*(a^4 + 4*a^3*b + 6*a^2*b^2 + 4*a*b^3 + b^4)*m)*y^4 - 4*(a^4 + 4*a^3*b + 6*a^2*b^2 + 4*a*b^3 + b^4)*m*y^2 + 4*(a^4 + 4*a^3*b + 6*a^2*b^2 + 4*a*b^3 + b^4)*m^2)*diff(chi_1(y), y, y))/((ch0^2 - 1)*y^4 + (ch0^2 - 1)*y^2 - 2*(ch0^2 - 1)*m) == 0

In [89]:
eq_chi1.lhs().denominator().simplify_full()

(ch0^2 - 1)*y^4 + (ch0^2 - 1)*y^2 - 2*(ch0^2 - 1)*m

In [90]:
eq_chi1 = eq_chi1.lhs().numerator().simplify_full() == 0
eq_chi1

((a^4 + 2*a^3*b - 2*a*b^3 - b^4)*ch0^3 - (a^4 + 2*a^3*b - 2*a*b^3 - b^4)*ch0)*y^4 - (((a^4 + 2*a^3*b + a^2*b^2)*ch0^3 - (a^4 + 2*a^3*b + a^2*b^2)*ch0)*y^8 + 2*((a^4 + 2*a^3*b + a^2*b^2)*ch0^3 - (a^4 + 2*a^3*b + a^2*b^2)*ch0)*y^6 + ((a^4 + 2*a^3*b + a^2*b^2)*ch0^3 - (a^4 + 2*a^3*b + a^2*b^2)*ch0 - 4*((a^4 + 2*a^3*b + a^2*b^2)*ch0^3 - (a^4 + 2*a^3*b + a^2*b^2)*ch0)*m)*y^4 - 4*((a^4 + 2*a^3*b + a^2*b^2)*ch0^3 - (a^4 + 2*a^3*b + a^2*b^2)*ch0)*m*y^2 + 4*((a^4 + 2*a^3*b + a^2*b^2)*ch0^3 - (a^4 + 2*a^3*b + a^2*b^2)*ch0)*m^2)*diff(Phi_1(y), y)^2 + (((a^2*b^2 + 2*a*b^3 + b^4)*ch0^3 - (a^2*b^2 + 2*a*b^3 + b^4)*ch0)*y^8 + 2*((a^2*b^2 + 2*a*b^3 + b^4)*ch0^3 - (a^2*b^2 + 2*a*b^3 + b^4)*ch0)*y^6 + ((a^2*b^2 + 2*a*b^3 + b^4)*ch0^3 - (a^2*b^2 + 2*a*b^3 + b^4)*ch0 - 4*((a^2*b^2 + 2*a*b^3 + b^4)*ch0^3 - (a^2*b^2 + 2*a*b^3 + b^4)*ch0)*m)*y^4 - 4*((a^2*b^2 + 2*a*b^3 + b^4)*ch0^3 - (a^2*b^2 + 2*a*b^3 + b^4)*ch0)*m*y^2 + 4*((a^2*b^2 + 2*a*b^3 + b^4)*ch0^3 - (a^2*b^2 + 2*a*b^3 + b^4)*ch0)*m^2)*diff(Psi_1(y), y)^2 - 4*((a^4 + 2*a^3*b - 2*a*b^3 - b^4)*ch0^3 - (a^4 + 2*a^3*b - 2*a*b^3 - b^4)*ch0)*m + 2*(2*(a^4 + 4*a^3*b + 6*a^2*b^2 + 4*a*b^3 + b^4)*y^7 + 3*(a^4 + 4*a^3*b + 6*a^2*b^2 + 4*a*b^3 + b^4)*y^5 + (a^4 + 4*a^3*b + 6*a^2*b^2 + 4*a*b^3 + b^4 - 4*(a^4 + 4*a^3*b + 6*a^2*b^2 + 4*a*b^3 + b^4)*m)*y^3 - 2*(a^4 + 4*a^3*b + 6*a^2*b^2 + 4*a*b^3 + b^4)*m*y)*diff(chi_1(y), y) + ((a^4 + 4*a^3*b + 6*a^2*b^2 + 4*a*b^3 + b^4)*y^8 + 2*(a^4 + 4*a^3*b + 6*a^2*b^2 + 4*a*b^3 + b^4)*y^6 + (a^4 + 4*a^3*b + 6*a^2*b^2 + 4*a*b^3 + b^4 - 4*(a^4 + 4*a^3*b + 6*a^2*b^2 + 4*a*b^3 + b^4)*m)*y^4 - 4*(a^4 + 4*a^3*b + 6*a^2*b^2 + 4*a*b^3 + b^4)*m*y^2 + 4*(a^4 + 4*a^3*b + 6*a^2*b^2 + 4*a*b^3 + b^4)*m^2)*diff(chi_1(y), y, y) == 0

We plug the solutions obtained previously for $\Phi_1(y)$ and $\Psi_1(y)$ in this equation:

In [91]:
eq_chi1 = eq_chi1.substitute_function(Phi_1, 
                                      Phi1_sol).substitute_function(Psi_1, 
                                                                    Psi1_sol)
eq_chi1 = eq_chi1.simplify_full()
eq_chi1

((a^4 + 2*a^3*b - 2*a*b^3 - b^4)*ch0^3 - (a^4 + 2*a^3*b - 2*a*b^3 - b^4)*ch0)*y^4 - ((a^4 + 2*a^3*b + a^2*b^2)*ch0^3 - (a^4 + 2*a^3*b + a^2*b^2)*ch0)*pf^2 + ((a^2*b^2 + 2*a*b^3 + b^4)*ch0^3 - (a^2*b^2 + 2*a*b^3 + b^4)*ch0)*qf^2 - 4*((a^4 + 2*a^3*b - 2*a*b^3 - b^4)*ch0^3 - (a^4 + 2*a^3*b - 2*a*b^3 - b^4)*ch0)*m + 2*(2*(a^4 + 4*a^3*b + 6*a^2*b^2 + 4*a*b^3 + b^4)*y^7 + 3*(a^4 + 4*a^3*b + 6*a^2*b^2 + 4*a*b^3 + b^4)*y^5 + (a^4 + 4*a^3*b + 6*a^2*b^2 + 4*a*b^3 + b^4 - 4*(a^4 + 4*a^3*b + 6*a^2*b^2 + 4*a*b^3 + b^4)*m)*y^3 - 2*(a^4 + 4*a^3*b + 6*a^2*b^2 + 4*a*b^3 + b^4)*m*y)*diff(chi_1(y), y) + ((a^4 + 4*a^3*b + 6*a^2*b^2 + 4*a*b^3 + b^4)*y^8 + 2*(a^4 + 4*a^3*b + 6*a^2*b^2 + 4*a*b^3 + b^4)*y^6 + (a^4 + 4*a^3*b + 6*a^2*b^2 + 4*a*b^3 + b^4 - 4*(a^4 + 4*a^3*b + 6*a^2*b^2 + 4*a*b^3 + b^4)*m)*y^4 - 4*(a^4 + 4*a^3*b + 6*a^2*b^2 + 4*a*b^3 + b^4)*m*y^2 + 4*(a^4 + 4*a^3*b + 6*a^2*b^2 + 4*a*b^3 + b^4)*m^2)*diff(chi_1(y), y, y) == 0

### Check of Eq. (4.30)

In [92]:
lhs = eq_chi1.lhs()
lhs = lhs.simplify_full()
lhs

((a^4 + 2*a^3*b - 2*a*b^3 - b^4)*ch0^3 - (a^4 + 2*a^3*b - 2*a*b^3 - b^4)*ch0)*y^4 - ((a^4 + 2*a^3*b + a^2*b^2)*ch0^3 - (a^4 + 2*a^3*b + a^2*b^2)*ch0)*pf^2 + ((a^2*b^2 + 2*a*b^3 + b^4)*ch0^3 - (a^2*b^2 + 2*a*b^3 + b^4)*ch0)*qf^2 - 4*((a^4 + 2*a^3*b - 2*a*b^3 - b^4)*ch0^3 - (a^4 + 2*a^3*b - 2*a*b^3 - b^4)*ch0)*m + 2*(2*(a^4 + 4*a^3*b + 6*a^2*b^2 + 4*a*b^3 + b^4)*y^7 + 3*(a^4 + 4*a^3*b + 6*a^2*b^2 + 4*a*b^3 + b^4)*y^5 + (a^4 + 4*a^3*b + 6*a^2*b^2 + 4*a*b^3 + b^4 - 4*(a^4 + 4*a^3*b + 6*a^2*b^2 + 4*a*b^3 + b^4)*m)*y^3 - 2*(a^4 + 4*a^3*b + 6*a^2*b^2 + 4*a*b^3 + b^4)*m*y)*diff(chi_1(y), y) + ((a^4 + 4*a^3*b + 6*a^2*b^2 + 4*a*b^3 + b^4)*y^8 + 2*(a^4 + 4*a^3*b + 6*a^2*b^2 + 4*a*b^3 + b^4)*y^6 + (a^4 + 4*a^3*b + 6*a^2*b^2 + 4*a*b^3 + b^4 - 4*(a^4 + 4*a^3*b + 6*a^2*b^2 + 4*a*b^3 + b^4)*m)*y^4 - 4*(a^4 + 4*a^3*b + 6*a^2*b^2 + 4*a*b^3 + b^4)*m*y^2 + 4*(a^4 + 4*a^3*b + 6*a^2*b^2 + 4*a*b^3 + b^4)*m^2)*diff(chi_1(y), y, y)

In [93]:
s = lhs.coefficient(diff(chi_1(y), y, 2))  # coefficient of chi_1''
s.factor()

(y^4 + y^2 - 2*m)^2*(a + b)^4

In [94]:
s1 = (lhs/s - diff(chi_1(y), y, 2)).simplify_full()
s1

(((a^2 - b^2)*ch0^3 - (a^2 - b^2)*ch0)*y^4 - (a^2*ch0^3 - a^2*ch0)*pf^2 + (b^2*ch0^3 - b^2*ch0)*qf^2 - 4*((a^2 - b^2)*ch0^3 - (a^2 - b^2)*ch0)*m + 2*(2*(a^2 + 2*a*b + b^2)*y^7 + 3*(a^2 + 2*a*b + b^2)*y^5 + (a^2 + 2*a*b + b^2 - 4*(a^2 + 2*a*b + b^2)*m)*y^3 - 2*(a^2 + 2*a*b + b^2)*m*y)*diff(chi_1(y), y))/((a^2 + 2*a*b + b^2)*y^8 + 2*(a^2 + 2*a*b + b^2)*y^6 + (a^2 + 2*a*b + b^2 - 4*(a^2 + 2*a*b + b^2)*m)*y^4 - 4*(a^2 + 2*a*b + b^2)*m*y^2 + 4*(a^2 + 2*a*b + b^2)*m^2)

In [95]:
b1 = s1.coefficient(diff(chi_1(y), y)).factor()
b1

2*(2*y^2 + 1)*y/(y^4 + y^2 - 2*m)

In [96]:
b2 = (s1 - b1*diff(chi_1(y), y)).simplify_full().factor()
b2

(a^2*y^4 - b^2*y^4 - a^2*pf^2 + b^2*qf^2 - 4*a^2*m + 4*b^2*m)*(ch0 + 1)*(ch0 - 1)*ch0/((y^4 + y^2 - 2*m)^2*(a + b)^2)

The equation for $\chi_1$ is thus:

In [97]:
eq_chi1 = diff(chi_1(y), y, 2) + b1*diff(chi_1(y), y) + b2 == 0
eq_chi1

2*(2*y^2 + 1)*y*diff(chi_1(y), y)/(y^4 + y^2 - 2*m) + (a^2*y^4 - b^2*y^4 - a^2*pf^2 + b^2*qf^2 - 4*a^2*m + 4*b^2*m)*(ch0 + 1)*(ch0 - 1)*ch0/((y^4 + y^2 - 2*m)^2*(a + b)^2) + diff(chi_1(y), y, y) == 0

Given that 
$$ \chi_1(y) = - \sin\Theta_0 \; \Theta_1(y) = - \sqrt{1-\chi_0^2}  \; \Theta_1(y)$$
and
$$\sin2\Theta_0 = 2\chi_0\sqrt{1-\chi_0^2}$$
we get for the following equation for $\Upsilon = \Theta_1'$ 
(defining $\Theta_2 := 2 \Theta_0$):

In [98]:
Y = function('Y', latex_name=r'\Upsilon')
Th2 = var('Th2', latex_name=r'\Theta_2', domain='real')
eq_Y = diff(Y(y), y) + b1*Y(y) \
       - b2/(1 - ch0)/(1 + ch0)/ch0*sin(Th2)/2 == 0
eq_Y

2*(2*y^2 + 1)*y*Y(y)/(y^4 + y^2 - 2*m) + 1/2*(a^2*y^4 - b^2*y^4 - a^2*pf^2 + b^2*qf^2 - 4*a^2*m + 4*b^2*m)*sin(Th2)/((y^4 + y^2 - 2*m)^2*(a + b)^2) + diff(Y(y), y) == 0

This agrees with Eq. (4.30) of the paper.

### Solving the equation for $\Upsilon := \Theta_1'$

In [99]:
Y_sol(y) = desolve(eq_Y, Y(y), ivar=y)

The solution involves an integral that SageMath is not capable to evaluate with the default integrator. Printing `Y_sol` provides the unvaluated form of the integral, in order to compute it by means of FriCAS:

In [100]:
print(Y_sol(y))

1/2*(2*_C - (a*sin(Th2) - b*sin(Th2))*y/(a + b) - integrate(-(a^2*pf^2 - b^2*qf^2 + (a^2 - b^2)*y^2 + 2*(a^2 - b^2)*m)/(y^4 + y^2 - 2*m), y)*sin(Th2)/(a^2 + 2*a*b + b^2))/(y^4 + y^2 - 2*m)


The solution involves some constant, denoted `_C` by SageMath. We rename it `C_1` and 
rewrite the above solution as

In [101]:
C_1 = var('C_1')
Integ(y) = function('Integ')(y)
Y_sol0(y) = 1/2*(2*C_1 - (a*sin(Th2) - b*sin(Th2))*y/(a + b) \
                 - Integ(y)*sin(Th2)/(a^2 + 2*a*b + b^2))/(y^4 + y^2 - 2*m)
Y_sol0(y)

1/2*(2*C_1 - (a*sin(Th2) - b*sin(Th2))*y/(a + b) - Integ(y)*sin(Th2)/(a^2 + 2*a*b + b^2))/(y^4 + y^2 - 2*m)

`Integ(y)` represents the integral $I(y)$, whose integrand, $F(y)$ say, is read from the
output of `print(Y_sol(Y))`:

In [102]:
F(y) = -(a^2*pf^2 - b^2*qf^2 + (a^2 - b^2)*y^2 + 2*(a^2 - b^2)*m)/(y^4 + y^2 - 2*m)
F(y)

-(a^2*pf^2 - b^2*qf^2 + (a^2 - b^2)*y^2 + 2*(a^2 - b^2)*m)/(y^4 + y^2 - 2*m)

We split the integral in two parts:
$$ I(y) = F_1 \; s_1(y) + F_2 \; s_2(y)$$
with 
$$ s_1(y) := \int^y \frac{\bar{y}^2}{\bar{y}^4 + \bar{y}^2 - 2m} \, \mathrm{d}\bar{y}, \qquad  s_2(y) := \int^y \frac{\mathrm{d}\bar{y}}{\bar{y}^4 + \bar{y}^2 - 2m} $$
and

In [103]:
F1 = -(a^2 - b^2)
F1

-a^2 + b^2

In [104]:
F2 = -(a^2*pf^2 - b^2*qf^2 + 2*(a^2 - b^2)*m)
F2

-a^2*pf^2 + b^2*qf^2 - 2*(a^2 - b^2)*m

Check:

In [105]:
bool(F(y) == F1*y^2/(y^4 + y^2 - 2*m) + F2/(y^4 + y^2 - 2*m))

True

Let us evaluate $s_1(y)$ by means of FriCAS:

In [106]:
s1 = integrate(y^2/(y^4 + y^2 - 2*m), y, algorithm='fricas')
s1

1/2*sqrt(1/2)*sqrt(-(sqrt(8*m + 1) + 1)/(8*m + 1))*log(sqrt(1/2)*sqrt(8*m + 1)*sqrt(-(sqrt(8*m + 1) + 1)/(8*m + 1)) + y) - 1/2*sqrt(1/2)*sqrt(-(sqrt(8*m + 1) + 1)/(8*m + 1))*log(-sqrt(1/2)*sqrt(8*m + 1)*sqrt(-(sqrt(8*m + 1) + 1)/(8*m + 1)) + y) - 1/2*sqrt(1/2)*sqrt((sqrt(8*m + 1) - 1)/(8*m + 1))*log(sqrt(1/2)*sqrt(8*m + 1)*sqrt((sqrt(8*m + 1) - 1)/(8*m + 1)) + y) + 1/2*sqrt(1/2)*sqrt((sqrt(8*m + 1) - 1)/(8*m + 1))*log(-sqrt(1/2)*sqrt(8*m + 1)*sqrt((sqrt(8*m + 1) - 1)/(8*m + 1)) + y)

In [107]:
s1 = s1.canonicalize_radical().simplify_log()
s1

1/4*(sqrt(2)*sqrt(sqrt(8*m + 1) - 1)*log((sqrt(2)*y - sqrt(sqrt(8*m + 1) - 1))/(sqrt(2)*y + sqrt(sqrt(8*m + 1) - 1))) + sqrt(2)*sqrt(-sqrt(8*m + 1) - 1)*log((sqrt(2)*y + sqrt(-sqrt(8*m + 1) - 1))/(sqrt(2)*y - sqrt(-sqrt(8*m + 1) - 1))))/sqrt(8*m + 1)

Check:

In [108]:
diff(s1, y).simplify_full()

y^2/(y^4 + y^2 - 2*m)

Similarly, we evaluate $s_2(y)$ by means of FriCAS:

In [109]:
s2 = integrate(1/(y^4 + y^2 - 2*m), y, algorithm='fricas')
s2

-1/4*sqrt(((8*m^2 + m)/sqrt(8*m^3 + m^2) + 1)/(8*m^2 + m))*log(1/2*(8*m - (8*m^2 + m)/sqrt(8*m^3 + m^2) + 1)*sqrt(((8*m^2 + m)/sqrt(8*m^3 + m^2) + 1)/(8*m^2 + m)) + 2*y) + 1/4*sqrt(((8*m^2 + m)/sqrt(8*m^3 + m^2) + 1)/(8*m^2 + m))*log(-1/2*(8*m - (8*m^2 + m)/sqrt(8*m^3 + m^2) + 1)*sqrt(((8*m^2 + m)/sqrt(8*m^3 + m^2) + 1)/(8*m^2 + m)) + 2*y) - 1/4*sqrt(-((8*m^2 + m)/sqrt(8*m^3 + m^2) - 1)/(8*m^2 + m))*log(1/2*(8*m + (8*m^2 + m)/sqrt(8*m^3 + m^2) + 1)*sqrt(-((8*m^2 + m)/sqrt(8*m^3 + m^2) - 1)/(8*m^2 + m)) + 2*y) + 1/4*sqrt(-((8*m^2 + m)/sqrt(8*m^3 + m^2) - 1)/(8*m^2 + m))*log(-1/2*(8*m + (8*m^2 + m)/sqrt(8*m^3 + m^2) + 1)*sqrt(-((8*m^2 + m)/sqrt(8*m^3 + m^2) - 1)/(8*m^2 + m)) + 2*y)

In [110]:
s2 = s2.canonicalize_radical().simplify_log()
s2

1/4*(sqrt(-8*m + sqrt(8*m + 1) - 1)*log((4*(8*m + 1)^(1/4)*sqrt(m)*y - sqrt(-8*m + sqrt(8*m + 1) - 1)*(sqrt(8*m + 1) + 1))/(4*(8*m + 1)^(1/4)*sqrt(m)*y + sqrt(-8*m + sqrt(8*m + 1) - 1)*(sqrt(8*m + 1) + 1))) + sqrt(8*m + sqrt(8*m + 1) + 1)*log((4*(8*m + 1)^(1/4)*sqrt(m)*y - sqrt(8*m + sqrt(8*m + 1) + 1)*(sqrt(8*m + 1) - 1))/(4*(8*m + 1)^(1/4)*sqrt(m)*y + sqrt(8*m + sqrt(8*m + 1) + 1)*(sqrt(8*m + 1) - 1))))/((8*m + 1)^(3/4)*sqrt(m))

Check:

In [111]:
diff(s2, y).simplify_full()

1/(y^4 + y^2 - 2*m)

In the above expressions for $s_1(y)$ and $s_2(y)$, there appears $\sqrt{1 + 8 m}$,
which can be rewritten
$$
    \sqrt{1 + 8 m} = 2 y_H^2 + 1 
$$
where $y_H$ is the positive root of $y_H^4 + y_H^2 - 2m = 0$. More precisely, we perform the following substitution:
$$
   m = \frac{1}{2} y_H^2 (y_H^2 + 1)
$$

In [112]:
yH = var('yH', latex_name=r'y_H', domain='real')
assume(yH > 0)
m_yH = yH^2*(yH^2 + 1)/2
s1 = s1.subs({m: m_yH}).canonicalize_radical().simplify_log()
s1

-1/2*(yH*log((y + yH)/(y - yH)) + I*sqrt(yH^2 + 1)*log((y - I*sqrt(yH^2 + 1))/(y + I*sqrt(yH^2 + 1))))/(2*yH^2 + 1)

In the second $\log$, we recognize the $\mathrm{arccot}$ function, via the identity
$$
    \mathrm{arccot}\,  x =  \frac{i}{2} \ln\left( \frac{x - i}{x + i} \right) . 
$$
Given that $\mathrm{arccot}\,  x = \pi/2 - \mathrm{arctan}\, x$, we use this identity as
$$
i \ln\left( \frac{x - i}{x + i} \right) = - 2 \, \mathrm{arctan}(x) + \pi
$$

Thus, we perform the following substitution, disregarding the additive constant $\pi$:

In [113]:
s1 = s1.subs({I*sqrt(yH^2 + 1)*log((y - I*sqrt(yH^2 + 1))/(y + I*sqrt(yH^2 + 1))):
              -2*sqrt(yH^2 + 1)*atan(y/sqrt(yH^2 + 1))})
s1

-1/2*(yH*log((y + yH)/(y - yH)) - 2*sqrt(yH^2 + 1)*arctan(y/sqrt(yH^2 + 1)))/(2*yH^2 + 1)

Let us check that we have indeed a primitive of $y\mapsto \frac{y^2}{y^4 + y^2 - 2m}$:

In [114]:
Ds1 = diff(s1, y).simplify_full()
Ds1

y^2/(y^4 - yH^4 + y^2 - yH^2)

In [115]:
yH_m = sqrt(sqrt(1 + 8*m) - 1)/sqrt(2)
Ds1.subs({yH: yH_m}).simplify_full()

y^2/(y^4 + y^2 - 2*m)

Similarly, let us express $s_2$ in terms of $y_H$:

In [116]:
s2 = s2.subs({m: m_yH}).canonicalize_radical().simplify_log()
s2

1/2*(I*yH*log((-I*yH^2 + sqrt(yH^2 + 1)*y - I)/(I*yH^2 + sqrt(yH^2 + 1)*y + I)) + sqrt(yH^2 + 1)*log((y - yH)/(y + yH)))/((2*yH^3 + yH)*sqrt(yH^2 + 1))

Again, we use the identity
$$
i \ln\left( \frac{x - i}{x + i} \right) = - 2 \, \mathrm{arctan}(x) + \pi
$$
to rewrite $s_2$ as

In [117]:
s2 = s2.subs({I*yH*log((-I*yH^2 + sqrt(yH^2 + 1)*y - I)/(I*yH^2 + sqrt(yH^2 + 1)*y + I)):
              -2*yH*atan(y/sqrt(yH^2 + 1))})
s2

-1/2*(2*yH*arctan(y/sqrt(yH^2 + 1)) - sqrt(yH^2 + 1)*log((y - yH)/(y + yH)))/((2*yH^3 + yH)*sqrt(yH^2 + 1))

Let us also replace $\ln\left(\frac{y - y_H}{y + y_H}\right)$ by $-\ln\left(\frac{y + y_H}{y - y_H}\right)$
in order to have the same log term as in $s_1(y)$:

In [118]:
s2 = s2.subs({log((y - yH)/(y + yH)): - log((y + yH)/(y - yH))})
s2

-1/2*(2*yH*arctan(y/sqrt(yH^2 + 1)) + sqrt(yH^2 + 1)*log((y + yH)/(y - yH)))/((2*yH^3 + yH)*sqrt(yH^2 + 1))

Let us check that we have indeed a primitive of $y\mapsto \frac{1}{y^4 + y^2 - 2m}$:

In [119]:
Ds2 = diff(s2, y).simplify_full()
Ds2

1/(y^4 - yH^4 + y^2 - yH^2)

In [120]:
Ds2.subs({yH: yH_m}).simplify_full()

1/(y^4 + y^2 - 2*m)

The full integral is thus

In [121]:
Integ0 = (F1*s1 + F2*s2).simplify_full()
Integ0

1/2*((a^2*pf^2 - b^2*qf^2 + (a^2 - b^2)*yH^2 + 2*(a^2 - b^2)*m)*sqrt(yH^2 + 1)*log((y + yH)/(y - yH)) - 2*((a^2 - b^2)*yH^3 - (a^2*pf^2 - b^2*qf^2 - a^2 + b^2 + 2*(a^2 - b^2)*m)*yH)*arctan(y/sqrt(yH^2 + 1)))/((2*yH^3 + yH)*sqrt(yH^2 + 1))

so that the solution is

In [122]:
Y_sol(y) = Y_sol0(y).subs({Integ(y): Integ0}).simplify_full()
Y_sol(y)

1/4*(2*((a^2*sin(Th2) - b^2*sin(Th2))*yH^3 - (a^2*pf^2*sin(Th2) - b^2*qf^2*sin(Th2) - a^2*sin(Th2) + b^2*sin(Th2) + 2*(a^2*sin(Th2) - b^2*sin(Th2))*m)*yH)*arctan(y/sqrt(yH^2 + 1)) + (4*(2*C_1*a^2 + 4*C_1*a*b + 2*C_1*b^2 - (a^2*sin(Th2) - b^2*sin(Th2))*y)*yH^3 + 2*(2*C_1*a^2 + 4*C_1*a*b + 2*C_1*b^2 - (a^2*sin(Th2) - b^2*sin(Th2))*y)*yH - (a^2*pf^2*sin(Th2) - b^2*qf^2*sin(Th2) + (a^2*sin(Th2) - b^2*sin(Th2))*yH^2 + 2*(a^2*sin(Th2) - b^2*sin(Th2))*m)*log((y + yH)/(y - yH)))*sqrt(yH^2 + 1))/((2*((a^2 + 2*a*b + b^2)*y^4 + (a^2 + 2*a*b + b^2)*y^2 - 2*(a^2 + 2*a*b + b^2)*m)*yH^3 + ((a^2 + 2*a*b + b^2)*y^4 + (a^2 + 2*a*b + b^2)*y^2 - 2*(a^2 + 2*a*b + b^2)*m)*yH)*sqrt(yH^2 + 1))

In [123]:
Y_sol(y).numerator().simplify_full()

2*((a^2*sin(Th2) - b^2*sin(Th2))*yH^3 - (a^2*pf^2*sin(Th2) - b^2*qf^2*sin(Th2) - a^2*sin(Th2) + b^2*sin(Th2) + 2*(a^2*sin(Th2) - b^2*sin(Th2))*m)*yH)*arctan(y/sqrt(yH^2 + 1)) + (4*(2*C_1*a^2 + 4*C_1*a*b + 2*C_1*b^2 - (a^2*sin(Th2) - b^2*sin(Th2))*y)*yH^3 + 2*(2*C_1*a^2 + 4*C_1*a*b + 2*C_1*b^2 - (a^2*sin(Th2) - b^2*sin(Th2))*y)*yH - (a^2*pf^2*sin(Th2) - b^2*qf^2*sin(Th2) + (a^2*sin(Th2) - b^2*sin(Th2))*yH^2 + 2*(a^2*sin(Th2) - b^2*sin(Th2))*m)*log((y + yH)/(y - yH)))*sqrt(yH^2 + 1)

In [124]:
Y_sol(y).denominator().factor()

4*(y^4 + y^2 - 2*m)*(2*yH^2 + 1)*sqrt(yH^2 + 1)*(a + b)^2*yH

Let us check that `Y_sol` is indeed a solution of the differential equation for $\Upsilon$:

In [125]:
eq_Y.substitute_function(Y, Y_sol).subs({yH: yH_m}).simplify_full()

0 == 0

In [126]:
print(Y_sol(y))

1/4*(2*((a^2*sin(Th2) - b^2*sin(Th2))*yH^3 - (a^2*pf^2*sin(Th2) - b^2*qf^2*sin(Th2) - a^2*sin(Th2) + b^2*sin(Th2) + 2*(a^2*sin(Th2) - b^2*sin(Th2))*m)*yH)*arctan(y/sqrt(yH^2 + 1)) + (4*(2*C_1*a^2 + 4*C_1*a*b + 2*C_1*b^2 - (a^2*sin(Th2) - b^2*sin(Th2))*y)*yH^3 + 2*(2*C_1*a^2 + 4*C_1*a*b + 2*C_1*b^2 - (a^2*sin(Th2) - b^2*sin(Th2))*y)*yH - (a^2*pf^2*sin(Th2) - b^2*qf^2*sin(Th2) + (a^2*sin(Th2) - b^2*sin(Th2))*yH^2 + 2*(a^2*sin(Th2) - b^2*sin(Th2))*m)*log((y + yH)/(y - yH)))*sqrt(yH^2 + 1))/((2*((a^2 + 2*a*b + b^2)*y^4 + (a^2 + 2*a*b + b^2)*y^2 - 2*(a^2 + 2*a*b + b^2)*m)*yH^3 + ((a^2 + 2*a*b + b^2)*y^4 + (a^2 + 2*a*b + b^2)*y^2 - 2*(a^2 + 2*a*b + b^2)*m)*yH)*sqrt(yH^2 + 1))


### Check of Eq. (4.31) (expression of $\Theta'_1 = \Upsilon$)

The term involving the constant $C_1$ agrees with that of Eq. (4.31):

In [127]:
s = Y_sol(y).coefficient(C_1).simplify_full()
s

1/(y^4 + y^2 - 2*m)

Let us remove it from $\Upsilon$ and divide the result by $\sin(2\Theta_0)$:

In [128]:
Y1 = ((Y_sol(y) - s*C_1)/sin(Th2)).simplify_full()
Y1

1/4*(2*((a^2 - b^2)*yH^3 - (a^2*pf^2 - b^2*qf^2 - a^2 + b^2 + 2*(a^2 - b^2)*m)*yH)*arctan(y/sqrt(yH^2 + 1)) - (4*(a^2 - b^2)*y*yH^3 + 2*(a^2 - b^2)*y*yH + (a^2*pf^2 - b^2*qf^2 + (a^2 - b^2)*yH^2 + 2*(a^2 - b^2)*m)*log((y + yH)/(y - yH)))*sqrt(yH^2 + 1))/((2*((a^2 + 2*a*b + b^2)*y^4 + (a^2 + 2*a*b + b^2)*y^2 - 2*(a^2 + 2*a*b + b^2)*m)*yH^3 + ((a^2 + 2*a*b + b^2)*y^4 + (a^2 + 2*a*b + b^2)*y^2 - 2*(a^2 + 2*a*b + b^2)*m)*yH)*sqrt(yH^2 + 1))

The coefficient of the arctan term is

In [129]:
s = Y1.coefficient(arctan(y/sqrt(yH^2 + 1))).simplify_full().factor()
s

-1/2*(a^2*pf^2 - b^2*qf^2 - a^2*yH^2 + b^2*yH^2 + 2*a^2*m - 2*b^2*m - a^2 + b^2)/((y^4 + y^2 - 2*m)*(2*yH^2 + 1)*sqrt(yH^2 + 1)*(a + b)^2)

The numerator of this term agrees with Eq. (4.31), once we express $m$ in terms of $y_H$:

In [130]:
s.numerator().subs({m: m_yH}).simplify_full()

-(a^2 - b^2)*yH^4 - a^2*pf^2 + b^2*qf^2 + a^2 - b^2

The denominator agrees with Eq. (4.31) as well:

In [131]:
s.denominator()

2*(y^4 + y^2 - 2*m)*(2*yH^2 + 1)*sqrt(yH^2 + 1)*(a + b)^2

Let us remove the arctan term from $\Upsilon$:

In [132]:
Y2 = (Y1 - s*arctan(y/sqrt(yH^2 + 1))).simplify_full()
Y2

-1/4*(4*(a^2 - b^2)*y*yH^3 + 2*(a^2 - b^2)*y*yH + (a^2*pf^2 - b^2*qf^2 + (a^2 - b^2)*yH^2 + 2*(a^2 - b^2)*m)*log((y + yH)/(y - yH)))/(2*((a^2 + 2*a*b + b^2)*y^4 + (a^2 + 2*a*b + b^2)*y^2 - 2*(a^2 + 2*a*b + b^2)*m)*yH^3 + ((a^2 + 2*a*b + b^2)*y^4 + (a^2 + 2*a*b + b^2)*y^2 - 2*(a^2 + 2*a*b + b^2)*m)*yH)

In [133]:
Y2.numerator().simplify_full()

-4*(a^2 - b^2)*y*yH^3 - 2*(a^2 - b^2)*y*yH - (a^2*pf^2 - b^2*qf^2 + (a^2 - b^2)*yH^2 + 2*(a^2 - b^2)*m)*log((y + yH)/(y - yH))

In [134]:
Y2.denominator().factor()

4*(y^4 + y^2 - 2*m)*(2*yH^2 + 1)*(a + b)^2*yH

The coefficient of the log term is

In [135]:
s = Y2.coefficient(log((y + yH)/(y - yH))).simplify_full().factor()
s

-1/4*(a^2*pf^2 - b^2*qf^2 + a^2*yH^2 - b^2*yH^2 + 2*a^2*m - 2*b^2*m)/((y^4 + y^2 - 2*m)*(2*yH^2 + 1)*(a + b)^2*yH)

The numerator and denominator both agree with Eq. (4.31):

In [136]:
s.numerator().subs({m: m_yH}).simplify_full()

-(a^2 - b^2)*yH^4 - a^2*pf^2 + b^2*qf^2 - 2*(a^2 - b^2)*yH^2

In [137]:
s.denominator()

4*(y^4 + y^2 - 2*m)*(2*yH^2 + 1)*(a + b)^2*yH

Given that 
$$ \mathrm{artanh}\, x = \frac{1}{2} \ln\left( \frac{1 + x}{1 - x} \right) $$
we have
$$
   \ln \left( \frac{x + 1}{x - 1} \right) = 2\, \mathrm{artanh}\left(\frac{1}{x}\right)
$$

Hence the term in $\ln\left(\frac{y + y_H}{y - y_H}\right)$ agrees with the corresponding term in Eq. (4.30).

Finally, the last term in $\Upsilon$ is

In [138]:
Y3 = (Y2 - s*log((y + yH)/(y - yH))).simplify_full()
Y3.factor()

-1/2*(a - b)*y/((y^4 + y^2 - 2*m)*(a + b))

This term agrees with Eq. (4.31), given the simplification
$\frac{a^2 - b^2}{(a + b)^2} = \frac{a - b}{a + b}$.

### Conjugate momenta

In [139]:
def conjugate_momenta(lagr, qs, var):
    r"""
    Compute the conjugate momenta from a given Lagrangian.

    INPUT:

    - ``lagr`` -- symbolic expression representing the Lagrangian density
    - ``qs`` -- either a single symbolic function or a list/tuple of
      symbolic functions, representing the `q`'s; these functions must
      appear in ``lagr`` up to at most their first derivatives
    - ``var`` -- either a single variable, typically `t` (1-dimensional
      problem) or a list/tuple of symbolic variables; in the latter case the
      time coordinate must the first one

    OUTPUT:

    - list of conjugate momenta; if only one function is involved, the
      single conjugate momentum is returned instead.

    """
    if not isinstance(qs, (list, tuple)):
        qs = [qs]
    if not isinstance(var, (list, tuple)):
        var = [var]
    n = len(qs)
    d = len(var)
    dqvt = [SR.var('qxxxx{}_t'.format(q)) for q in qs]
    subs = {diff(qs[i](*var), var[0]): dqvt[i] for i in range(n)}
    subs_inv = {dqvt[i]: diff(qs[i](*var), var[0]) for i in range(n)}
    lg = lagr.substitute(subs)
    ps = [diff(lg, dotq).simplify_full().substitute(subs_inv) for dotq in dqvt]
    if n == 1:
        return ps[0]
    return ps

In [140]:
pis = conjugate_momenta(L_2, [Phi_1, Psi_1], y)
pis

[-(a^2*ch0^2 - a^2)*y^4*diff(Phi_1(y), y) - (a^2*ch0^2 - a^2)*y^2*diff(Phi_1(y), y) + 2*(a^2*ch0^2 - a^2)*m*diff(Phi_1(y), y),
 b^2*ch0^2*y^4*diff(Psi_1(y), y) + b^2*ch0^2*y^2*diff(Psi_1(y), y) - 2*b^2*ch0^2*m*diff(Psi_1(y), y)]

$\pi^y_\Phi$:

In [141]:
pi_Phi_y = (pis[0]/a).substitute_function(Phi_1, Phi1_sol).simplify_full()
pi_Phi_y

-(a*ch0^2 - a)*pf

$\pi_\Psi^y$:

In [142]:
pi_Psi_y = (pis[1]/b).substitute_function(Psi_1, Psi1_sol).simplify_full()
pi_Psi_y

b*ch0^2*qf

### Check of Eq. (4.33)

We start from $\pi^y_\Theta$ as given by Eq. (4.32):

In [143]:
pi_Theta = ((y^4 + y^2 - 2*m)*(a + b)^2*Y_sol(y)).simplify_full()
pi_Theta 

1/4*(2*((a^2*sin(Th2) - b^2*sin(Th2))*yH^3 - (a^2*pf^2*sin(Th2) - b^2*qf^2*sin(Th2) - a^2*sin(Th2) + b^2*sin(Th2) + 2*(a^2*sin(Th2) - b^2*sin(Th2))*m)*yH)*arctan(y/sqrt(yH^2 + 1)) + (4*(2*C_1*a^2 + 4*C_1*a*b + 2*C_1*b^2 - (a^2*sin(Th2) - b^2*sin(Th2))*y)*yH^3 + 2*(2*C_1*a^2 + 4*C_1*a*b + 2*C_1*b^2 - (a^2*sin(Th2) - b^2*sin(Th2))*y)*yH - (a^2*pf^2*sin(Th2) - b^2*qf^2*sin(Th2) + (a^2*sin(Th2) - b^2*sin(Th2))*yH^2 + 2*(a^2*sin(Th2) - b^2*sin(Th2))*m)*log((y + yH)/(y - yH)))*sqrt(yH^2 + 1))/((2*yH^3 + yH)*sqrt(yH^2 + 1))

Let us perform an expansion in $1/y$ for $y\rightarrow +\infty$:

In [144]:
u = var('u')
assume(u > 0)
s = pi_Theta.subs({y: 1/u}).simplify_log()
s = s.taylor(u, 0, 2)
s = s.subs({u: 1/y})
s

-1/2*(a^2*sin(Th2) - b^2*sin(Th2))*y - 1/2*(a^2*sin(Th2) - b^2*sin(Th2))/y - 1/4*(pi*a^2*pf^2*sin(Th2) - pi*b^2*qf^2*sin(Th2) - pi*a^2*sin(Th2) + pi*b^2*sin(Th2) - (pi*a^2*sin(Th2) - pi*b^2*sin(Th2))*yH^2 + 2*(pi*a^2*sin(Th2) - pi*b^2*sin(Th2))*m - 4*(C_1*a^2 + 2*C_1*a*b + C_1*b^2 + 2*(C_1*a^2 + 2*C_1*a*b + C_1*b^2)*yH^2)*sqrt(yH^2 + 1))/((2*yH^2 + 1)*sqrt(yH^2 + 1))

We consider $\frac{\pi^y_\Theta}{\sin(2\Theta_0)}$:

In [145]:
s1 = (s/sin(Th2)).expand()
s1

-1/4*pi*a^2*pf^2/((2*yH^2 + 1)*sqrt(yH^2 + 1)) + 1/4*pi*b^2*qf^2/((2*yH^2 + 1)*sqrt(yH^2 + 1)) + 1/4*pi*a^2*yH^2/((2*yH^2 + 1)*sqrt(yH^2 + 1)) - 1/4*pi*b^2*yH^2/((2*yH^2 + 1)*sqrt(yH^2 + 1)) - 1/2*a^2*y + 1/2*b^2*y + 2*C_1*a^2*yH^2/((2*yH^2 + 1)*sin(Th2)) + 4*C_1*a*b*yH^2/((2*yH^2 + 1)*sin(Th2)) + 2*C_1*b^2*yH^2/((2*yH^2 + 1)*sin(Th2)) - 1/2*pi*a^2*m/((2*yH^2 + 1)*sqrt(yH^2 + 1)) + 1/2*pi*b^2*m/((2*yH^2 + 1)*sqrt(yH^2 + 1)) + 1/4*pi*a^2/((2*yH^2 + 1)*sqrt(yH^2 + 1)) - 1/4*pi*b^2/((2*yH^2 + 1)*sqrt(yH^2 + 1)) - 1/2*a^2/y + 1/2*b^2/y + C_1*a^2/((2*yH^2 + 1)*sin(Th2)) + 2*C_1*a*b/((2*yH^2 + 1)*sin(Th2)) + C_1*b^2/((2*yH^2 + 1)*sin(Th2))

The term in factor of $C_1$ is

In [146]:
s1.coefficient(C_1).factor()

(a + b)^2/sin(Th2)

Hence this terms agrees with Eq. (4.32).
We remove it from the main term:

In [147]:
s2 = (s1 - s1.coefficient(C_1)*C_1).simplify_full()
s2

-1/4*(4*((a^2 - b^2)*y^2 + a^2 - b^2)*yH^4 + 2*(a^2 - b^2)*y^2 + 6*((a^2 - b^2)*y^2 + a^2 - b^2)*yH^2 + 2*a^2 - 2*b^2 - ((pi*a^2 - pi*b^2)*y*yH^2 - (pi*a^2*pf^2 - pi*b^2*qf^2 - pi*a^2 + pi*b^2 + 2*(pi*a^2 - pi*b^2)*m)*y)*sqrt(yH^2 + 1))/(2*y*yH^4 + 3*y*yH^2 + y)

In [148]:
s2.numerator().simplify_full()

-4*((a^2 - b^2)*y^2 + a^2 - b^2)*yH^4 - 2*(a^2 - b^2)*y^2 - 6*((a^2 - b^2)*y^2 + a^2 - b^2)*yH^2 - 2*a^2 + 2*b^2 + ((pi*a^2 - pi*b^2)*y*yH^2 - (pi*a^2*pf^2 - pi*b^2*qf^2 - pi*a^2 + pi*b^2 + 2*(pi*a^2 - pi*b^2)*m)*y)*sqrt(yH^2 + 1)

In [149]:
s2.denominator().factor()

4*(2*yH^2 + 1)*(yH^2 + 1)*y

Let divide both the numerator and denominator by $y$

In [150]:
s2n = (s2.numerator()/y).expand()
s2n

-4*a^2*y*yH^4 + 4*b^2*y*yH^4 - pi*sqrt(yH^2 + 1)*a^2*pf^2 + pi*sqrt(yH^2 + 1)*b^2*qf^2 + pi*sqrt(yH^2 + 1)*a^2*yH^2 - pi*sqrt(yH^2 + 1)*b^2*yH^2 - 6*a^2*y*yH^2 + 6*b^2*y*yH^2 - 4*a^2*yH^4/y + 4*b^2*yH^4/y - 2*pi*sqrt(yH^2 + 1)*a^2*m + 2*pi*sqrt(yH^2 + 1)*b^2*m + pi*sqrt(yH^2 + 1)*a^2 - pi*sqrt(yH^2 + 1)*b^2 - 2*a^2*y + 2*b^2*y - 6*a^2*yH^2/y + 6*b^2*yH^2/y - 2*a^2/y + 2*b^2/y

In [151]:
s2d = (s2.denominator()/y).factor()
s2d

4*(2*yH^2 + 1)*(yH^2 + 1)

The coefficient of the term in $y$ is

In [152]:
s = s2n.coefficient(y).factor()
s/s2d

-1/2*(a + b)*(a - b)

This is in agreement with Eq. (4.33).

We remove it:

In [153]:
s3n = (s2n - s*y).simplify_full().expand()
s3n

-pi*sqrt(yH^2 + 1)*a^2*pf^2 + pi*sqrt(yH^2 + 1)*b^2*qf^2 + pi*sqrt(yH^2 + 1)*a^2*yH^2 - pi*sqrt(yH^2 + 1)*b^2*yH^2 - 4*a^2*yH^4/y + 4*b^2*yH^4/y - 2*pi*sqrt(yH^2 + 1)*a^2*m + 2*pi*sqrt(yH^2 + 1)*b^2*m + pi*sqrt(yH^2 + 1)*a^2 - pi*sqrt(yH^2 + 1)*b^2 - 6*a^2*yH^2/y + 6*b^2*yH^2/y - 2*a^2/y + 2*b^2/y

The coefficient of the term in $1/y$ is

In [154]:
s = s3n.coefficient(y^(-1)).factor()
s/s2d

-1/2*(a + b)*(a - b)

This is in agreement with Eq. (4.33).

Finally the remaining term is

In [155]:
s4n = (s3n - s/y).simplify_full().expand()
s4n

-pi*sqrt(yH^2 + 1)*a^2*pf^2 + pi*sqrt(yH^2 + 1)*b^2*qf^2 + pi*sqrt(yH^2 + 1)*a^2*yH^2 - pi*sqrt(yH^2 + 1)*b^2*yH^2 - 2*pi*sqrt(yH^2 + 1)*a^2*m + 2*pi*sqrt(yH^2 + 1)*b^2*m + pi*sqrt(yH^2 + 1)*a^2 - pi*sqrt(yH^2 + 1)*b^2

In [156]:
s4n.factor()

-pi*(a^2*pf^2 - b^2*qf^2 - a^2*yH^2 + b^2*yH^2 + 2*a^2*m - 2*b^2*m - a^2 + b^2)*sqrt(yH^2 + 1)

In [157]:
s = s4n.factor()/s2d
s

-1/4*pi*(a^2*pf^2 - b^2*qf^2 - a^2*yH^2 + b^2*yH^2 + 2*a^2*m - 2*b^2*m - a^2 + b^2)/((2*yH^2 + 1)*sqrt(yH^2 + 1))

In [158]:
s.subs({m: m_yH}).factor()

-1/4*pi*(a^2*yH^4 - b^2*yH^4 + a^2*pf^2 - b^2*qf^2 - a^2 + b^2)/((2*yH^2 + 1)*sqrt(yH^2 + 1))

The denominator clearly agrees with Eq. (4.33).

**Conclusion:** we have full agreement with Eq. (4.33).